In [1]:
import warnings
warnings.filterwarnings('ignore')

___
# Merge csv files for ETF shares, CME Open Interest, and CFTC COT reports.
___

### Usage:
Run all the cells in this workbook after you have run all of the "build" notebooks in this project

### Main Graphs:
The graphs that follow the header ```COT vs Market Graphs``` show the graph of the lastest COT (new format) for the main physical commodities vs a graph of the settlement prices for those commodities, or for an ETF that closely tracts those commodities (think Comex GC vs the ETF GLD).


In [58]:
import pandas as pd
from pandas_datareader import data as pdr
import numpy as np
import sys
import os
abs_folders = [os.path.abspath(d) for d in ['./','../']]
for af in abs_folders:
    if  not af in sys.path:
        sys.path.append(af)
from cme_open_interest import db_info

import datetime
%matplotlib inline
import matplotlib.pyplot as plt
import plotly.graph_objs as go
from plotly.offline import iplot
from plotly.offline import  init_notebook_mode, iplot
init_notebook_mode(connected=True)

import zipfile
import urllib.request
from PIL import Image
import jupyter_utilities as ju
import importlib
import pandasql as psql
import traceback
import pdb

# Make important folders
TEMP_FOLDER = './temp_folder'
try:
    os.mkdir(TEMP_FOLDER)
except:
    pass
SAVE_IMAGE_FOLDER = f'{TEMP_FOLDER}/gold'
try:
    os.mkdir(SAVE_IMAGE_FOLDER)
except:
    pass

def to_int(s,print_full_exception=False):
    try:
        return int(float(str(s)))
    except Exception as e:
        print(f'to_int exception on value:{s}')
        if print_full_exception:
            traceback.print_exc()
        return None

pd.set_option('display.max_colwidth',1000)
if os.path.abspath('../')  not in sys.path:
    if '.' not in sys.path:
        sys.path.append(os.path.abspath('../'))
import barchart_api as bcapi

cme_csv_save_folder = './cme_oi_data'
cot_data_path = './cot_net_new_history.csv'
etf_data_path = './etf_cap_hist.csv'

In [3]:
# importlib.reload(ju)

In [60]:
opttab = 'sec_schema.options_table'
futtab = 'sec_schema.underlying_table'

pga = db_info.get_db_info()
print(f"futtab max date: {pga.get_sql(f'select max(settle_date) from {futtab}')}")
print(f"opttab max date: {pga.get_sql(f'select max(settle_date) from {opttab}')}")


  sec_db
futtab max date:         max
0  20200512
opttab max date:         max
0  20200512


### Define commodity and etf identifiers in the csv files

In [76]:
OI_ID_GOLD = 'GOLD FUTURES'
OI_ID_SILVER = 'SILVER FUTURES'
OI_ID_CL = 'CRUDE OIL LIGHT SWEET FUTURES'
OI_ID_NG = 'NATURAL GAS FUTURES'
OI_ID_10Y = '10Y NOTE FUTURE'
OI_ID_SPY = 'E-MINI S&P 500 FUTURE'
OI_ID_SOYB = 'SOYBEAN FUTURE'
OI_ID_SOYO = 'SOYBEAN OIL FUTURE'
OI_ID_CORN = 'CORN FUTURE'
OI_ID_WHEAT = 'CHICAGO SRW WHEAT FUTURE'
OI_ID_COTTON = 'COTTON FUTURES'
OI_ID_EURO = 'EURO FX FUTURE'
OI_ID_ED = 'EURODOLLAR FUTURE'
OI_ID_HG = 'HIGH GRADE COPPER FUTURES'
OI_ID_PL = 'PLATINUM FUTURES'
OI_ID_SUGAR = 'SUGAR 11 FUTURES'
OI_ID_COCOA = 'COCOA FUTURES'

COT_ID_GOLD= 'GOLD - COMMODITY EXCHANGE INC.'
COT_ID_SILVER= 'SILVER - COMMODITY EXCHANGE INC.'
# COT_ID_CL = 'CRUDE OIL, LIGHT SWEET'
COT_ID_CL = 'CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE'
COT_ID_NG = 'NATURAL GAS - NEW YORK MERCANTILE EXCHANGE'
COT_ID_10Y = '10-YEAR U.S. TREASURY NOTES - CHICAGO BOARD OF TRADE'
COT_ID_SPY = 'E-MINI S&P 500 STOCK INDEX - CHICAGO MERCANTILE EXCHANGE'
COT_ID_SOYB = 'SOYBEANS - CHICAGO BOARD OF TRADE'
COT_ID_SOYO = 'SOYBEAN OIL - CHICAGO BOARD OF TRADE'
# COT_ID_WHEAT = 'WHEAT - CHICAGO BOARD OF TRADE'
COT_ID_COTTON = 'COTTON NO. 2 - ICE FUTURES U.S.'
COT_ID_WHEAT = 'WHEAT-SRW - CHICAGO BOARD OF TRADE'
COT_ID_CORN = 'CORN - CHICAGO BOARD OF TRADE'
COT_ID_EURO = 'EURO FX - CHICAGO MERCANTILE EXCHANGE'
COT_ID_ED = '3-MONTH EURODOLLARS - CHICAGO MERCANTILE EXCHANGE'
COT_ID_HG = 'COPPER-GRADE #1 - COMMODITY EXCHANGE INC.'
COT_ID_PL = 'PLATINUM - NEW YORK MERCANTILE EXCHANGE'
COT_ID_SUGAR = 'SUGAR NO. 11 - ICE FUTURES U.S.'
COT_ID_COCOA = 'COCOA - ICE FUTURES U.S.'

ETF_ID_GOLD = 'GLD'
ETF_ID_SILVER = 'SLV'
ETF_ID_CL = 'USO'
ETF_ID_NG = 'UNG'
ETF_ID_10Y = 'AGG'
ETF_ID_SPY = 'SPY'
ETF_ID_COTTON = 'BAL'
ETF_ID_SOYB = 'ZSZ99'#'ZSY00'
ETF_ID_SOYO = 'ZLZ99'#'ZLY00'
ETF_ID_WHEAT = 'ZWZ99'#'ZWY00'#'WEAT'
ETF_ID_CORN = 'CORN'
ETF_ID_EURO = 'FXE'
ETF_ID_ED = 'BSV'
ETF_ID_HG = 'CPER'
ETF_ID_PL = 'PPLT'
ETF_ID_SUGAR = 'SGG'
ETF_ID_COCOA = 'NIB'

ETF_SHARES_DIVISOR_GOLD = 1000
ETF_SHARES_DIVISOR_SILVER = 5000
ETF_SHARES_DIVISOR_10Y = 1000
ETF_SHARES_DIVISOR_SPY = 500
ETF_SHARES_DIVISOR_COTTON = 50000
ETF_SHARES_DIVISOR_SOYB = 5000
ETF_SHARES_DIVISOR_SOYO = 1
ETF_SHARES_DIVISOR_WHEAT = 5000
ETF_SHARES_DIVISOR_CORN = 5000
ETF_SHARES_DIVISOR_EURO = 1000
ETF_SHARES_DIVISOR_CL = 4000
ETF_SHARES_DIVISOR_NG = 1250
ETF_SHARES_DIVISOR_ED = 1000000
ETF_SHARES_DIVISOR_HG = 2500
ETF_SHARES_DIVISOR_PL = 500
ETF_SHARES_DIVISOR_SUGAR = int((112000/100)/3)
ETF_SHARES_DIVISOR_COCOA = 100


ID_DICT = {
    'gold':{'OI':OI_ID_GOLD,'COT':COT_ID_GOLD,'ETF':ETF_ID_GOLD,'ETF_DIVISOR':ETF_SHARES_DIVISOR_GOLD},
    'silver':{'OI':OI_ID_SILVER,'COT':COT_ID_SILVER,'ETF':ETF_ID_SILVER,'ETF_DIVISOR':ETF_SHARES_DIVISOR_SILVER},
#     '10Y':{'OI':OI_ID_10Y,'COT':COT_ID_10Y,'ETF':ETF_ID_10Y,'ETF_DIVISOR':ETF_SHARES_DIVISOR_10Y},
#     'spy':{'OI':OI_ID_SPY,'COT':COT_ID_SPY,'ETF':ETF_ID_SPY,'ETF_DIVISOR':ETF_SHARES_DIVISOR_SPY},
    'cotton':{'OI':OI_ID_COTTON,'COT':COT_ID_COTTON,'ETF':ETF_ID_COTTON,'ETF_DIVISOR':ETF_SHARES_DIVISOR_COTTON},
    'soyb':{'OI':OI_ID_SOYB,'COT':COT_ID_SOYB,'ETF':ETF_ID_SOYB,'ETF_DIVISOR':ETF_SHARES_DIVISOR_SOYB},
    'soyo':{'OI':OI_ID_SOYO,'COT':COT_ID_SOYO,'ETF':ETF_ID_SOYO,'ETF_DIVISOR':ETF_SHARES_DIVISOR_SOYO},
    'wheat':{'OI':OI_ID_WHEAT,'COT':COT_ID_WHEAT,'ETF':ETF_ID_WHEAT,'ETF_DIVISOR':ETF_SHARES_DIVISOR_WHEAT},
    'corn':{'OI':OI_ID_CORN,'COT':COT_ID_CORN,'ETF':ETF_ID_CORN,'ETF_DIVISOR':ETF_SHARES_DIVISOR_CORN},
#     'euro':{'OI':OI_ID_EURO,'COT':COT_ID_EURO,'ETF':ETF_ID_EURO,'ETF_DIVISOR':ETF_SHARES_DIVISOR_EURO},
    'cl':{'OI':OI_ID_CL,'COT':COT_ID_CL,'ETF':ETF_ID_CL,'ETF_DIVISOR':ETF_SHARES_DIVISOR_CL},
    'ng':{'OI':OI_ID_NG,'COT':COT_ID_NG,'ETF':ETF_ID_NG,'ETF_DIVISOR':ETF_SHARES_DIVISOR_NG},
#     'ed':{'OI':OI_ID_ED,'COT':COT_ID_ED,'ETF':ETF_ID_ED,'ETF_DIVISOR':ETF_SHARES_DIVISOR_ED},
    'hg':{'OI':OI_ID_HG,'COT':COT_ID_HG,'ETF':ETF_ID_HG,'ETF_DIVISOR':ETF_SHARES_DIVISOR_HG},
    'pl':{'OI':OI_ID_PL,'COT':COT_ID_PL,'ETF':ETF_ID_PL,'ETF_DIVISOR':ETF_SHARES_DIVISOR_PL},
    'sugar':{'OI':OI_ID_SUGAR,'COT':COT_ID_SUGAR,'ETF':ETF_ID_SUGAR,'ETF_DIVISOR':ETF_SHARES_DIVISOR_SUGAR},
    'cocoa':{'OI':OI_ID_COCOA,'COT':COT_ID_COCOA,'ETF':ETF_ID_COCOA,'ETF_DIVISOR':ETF_SHARES_DIVISOR_COCOA},
}


YEAR_OFFSET = 0 if datetime.datetime.now() > datetime.datetime(2020,1,10) else 1

In [91]:
ID_DICT['wheat']['ETF']

'ZWZ99'

___
## Define help access routines
___

In [77]:
# COT helpers
def df_cot_by_name(dict_id='cl',df_cot=None):
    dfc = df_cot2 if df_cot is None else df_cot
    cot_id = ID_DICT[dict_id]['COT']
    return dfc[dfc.Market_and_Exchange_Names==cot_id]


___
### Get cme open interest, COT and ETF data from csv files
___

In [78]:
import traceback
df_oi = None
last_year = int(datetime.datetime.now().year)
years = np.linspace(2013,last_year-YEAR_OFFSET,last_year-2013+1,dtype=int)
df_oi = None
for y in years:
    df_temp = pd.read_csv(f'{cme_csv_save_folder}/cme_open_interest_{y}.csv')
    df_temp = df_temp[~df_temp.Open_Interest.isnull()]
    if df_oi is None:
        df_oi = df_temp.copy()
    else:
        df_oi = df_oi.append(df_temp,ignore_index=True)
        df_oi.index = list(range(len(df_oi)))
df_oi = df_oi[~df_oi.Total_Volume.isnull()]
df_oi.ExPit_Volume = df_oi.ExPit_Volume.fillna(0)
df_oi = df_oi[~df_oi.Open_Interest.astype(str).str.contains('T')]
df_oi.Open_Interest = df_oi.Open_Interest.apply(to_int)
df_oi.Total_Volume = df_oi.Total_Volume.apply(to_int)
print(f'oi length:{len(df_oi)}')
df_etf = pd.read_csv(etf_data_path)
df_etf['trade_date'] = df_etf.date.apply(ju.str_to_yyyymmdd)
print(f'etf length:{len(df_etf)}')
df_cot2 = pd.read_csv(cot_data_path)
df_cot2.As_of_Date_In_Form_YYMMDD = df_cot2.As_of_Date_In_Form_YYMMDD.apply(ju.str_to_date)
df_cot2.Market_and_Exchange_Names = df_cot2.Market_and_Exchange_Names.str.strip() 
print(f'cot length:{len(df_cot2)}')


oi length:1595623
etf length:23034
cot length:57009


### For some of the ETF's, get the data from yahoo, and ignore the shares data

In [79]:
def fetch_history(symbol,dt_beg,dt_end):
    df = pdr.DataReader(symbol, 'yahoo', dt_beg, dt_end)
    df['date'] = df.index
    df.date = df.date.apply(lambda d: str(d)[0:4] + "-" + str(d)[5:7] + "-" + str(d)[8:10])
    df['trade_date'] = df.date.apply(lambda d: int(str(d)[0:4] + str(d)[5:7] + str(d)[8:10]))
    df = df.sort_values('date')
    df.index = list(range(len(df)))
    # make adj close the close
    df['nav'] = df['Adj Close']
    df['symbol'] = symbol
    df['shares'] = 0
    df = df[['symbol','date','nav','shares','trade_date']]
    return df

    

In [80]:
df_soyb = fetch_history(ETF_ID_SUGAR,datetime.datetime(2015,1,1),datetime.datetime(2020,12,31))
# print(df_etf.tail())
print(df_soyb.tail())
print(df_soyb.head())
# df_etf = df_etf.append(df_soyb,ignore_index=True)

    symbol        date        nav  shares  trade_date
574    SGG  2020-05-07  33.325001       0    20200507
575    SGG  2020-05-08  33.195000       0    20200508
576    SGG  2020-05-11  32.664001       0    20200511
577    SGG  2020-05-12  32.856998       0    20200512
578    SGG  2020-05-13  32.877300       0    20200513
  symbol        date        nav  shares  trade_date
0    SGG  2018-01-25  49.790001       0    20180125
1    SGG  2018-01-26  49.790001       0    20180126
2    SGG  2018-01-29  49.790001       0    20180129
3    SGG  2018-01-30  49.790001       0    20180130
4    SGG  2018-01-31  49.630001       0    20180131


In [81]:
def get_nasdaq_commod(commod='ZL'):
    df_zl = pd.read_csv(f'https://www.nasdaq.com/api/v1/historical/{commod}/commodities/2015-11-15/2022-12-15')
#     df_soyo = pd.DataFrame({'date':df_zl.as_matrix()[:,0],'nav':df_zl.as_matrix()[:,1],'shares':0})
    df_soyo = pd.DataFrame({'date':df_zl.values[:,0],'nav':df_zl.values[:,1],'shares':0})
    df_soyo['symbol'] = 'SOYO'
    df_soyo['date'] = df_soyo.date.apply(lambda s: s[6:10] + '-' + s[0:2] + '-' + s[3:5])
    df_soyo  = df_soyo.sort_values('date')
    df_soyo['trade_date'] = df_soyo.date.apply(lambda s: int(s.replace('-','')))
    return df_soyo[['symbol','date','nav','shares','trade_date']]

In [82]:
ETF_ID_SOYO,ETF_ID_SOYO[-3:]

('ZLZ99', 'Z99')

In [83]:
def get_barchart_commod(commod='ZL'):
    sql = f"""
    with 
    f1 as (
        select * from {futtab} where symbol = '{commod}Z99'
    )
    select * from f1
    """
    df = pga.get_sql(sql)
    df['date'] = df.settle_date.apply(lambda v: f"{str(v)[0:4]}-{str(v)[4:6]}-{str(v)[6:8]}")
    df['nav'] = df.close
    df['trade_date'] = df.settle_date
    df['shares'] = 0

    df = df[['symbol','date','nav','shares','trade_date']]
    return df    

In [84]:
df_wheat = get_barchart_commod('ZW')
df_wheat.tail()

symbol        date    nav  shares  trade_date
2414  ZWZ99  2020-05-06  539.0       0    20200506
2415  ZWZ99  2020-05-07  544.0       0    20200507
2416  ZWZ99  2020-05-08  544.0       0    20200508
2417  ZWZ99  2020-05-11  539.0       0    20200511
2418  ZWZ99  2020-05-12  537.0       0    20200512

In [85]:
# get_nasdaq_commod(ETF_ID_SOYO[:2])

### Find identifier strings for specific Open Interest and COT rows in their respective DataFrames
1. Enter values for oi_key_word, cot_key_word and etf_key_word below
2. Choose the product/market_and_exchange_name/symbol that has the highest open_interest or volume

In [100]:
import pdb
def create_merged_df(commod_to_use):
    global df_oi,df_etf,df_cot2
    # step 1 set up ID's
    OI_ID = ID_DICT[commod_to_use]['OI']
    COT_ID = ID_DICT[commod_to_use]['COT']
    ETF_ID = ID_DICT[commod_to_use]['ETF']
    ETF_DIVISOR = ID_DICT[commod_to_use]['ETF_DIVISOR']
    #Step 2: make sure ID's produce only one contract
    oi_key_word = OI_ID.lower()
    cot_key_word = COT_ID.lower()
    etf_key_word = ETF_ID.lower()

    l = (list(filter(lambda s: oi_key_word == str(s).lower(),df_oi.Product_Description.unique())))
    df_oi_sub = df_oi[df_oi.Product_Description.isin(l)][['Product_Description','Open_Interest']]
    df_oi_gb = df_oi_sub.groupby('Product_Description',as_index=False).sum()

    l = (list(filter(lambda s: cot_key_word == str(s).lower(),df_cot2.Market_and_Exchange_Names.unique())))
    df_cot_single = df_cot2[df_cot2.Market_and_Exchange_Names==COT_ID]
    df_cot_sub = df_cot2[df_cot2.Market_and_Exchange_Names.isin(l)][['Market_and_Exchange_Names','Open_Interest_All']]
    df_cot_gb = df_cot_sub.groupby('Market_and_Exchange_Names',as_index=False).sum()

    l = (list(filter(lambda s: etf_key_word == str(s).lower(),df_etf.symbol.unique())))
    dtmin = str(df_cot_single.As_of_Date_In_Form_YYMMDD.min())[0:10]
    dtmax = str(datetime.datetime.now())[0:10]
    #pdb.set_trace()
    if ETF_ID[-3:] == 'Y00':
        print(f'using get_nasdaq_commod for {ETF_ID}')
        df_etf_single = get_nasdaq_commod(ETF_ID[:2])
    elif ETF_ID[-3:] == 'Z99':
        print(f'using get_barchart_commod for {ETF_ID}')
        df_etf_single = get_barchart_commod(ETF_ID[:2])
    else:
        df_etf_single = fetch_history(ETF_ID,dtmin,dtmax)
    df_etf_gb = df_etf_single.groupby('symbol',as_index=False).sum()
    

    if len(df_oi_gb) + len(df_cot_gb) + len(df_etf_gb) == 3:
        print(f"all ID's for commodity: {commod_to_use} are OK")
    else:
        print(f"!!!!! ALL ID's FOR COMMODITY: {commod_to_use} ARE NOT OK!!!!!!")
        print(f'oi is OK: {len(df_oi_gb)==1}')
        print(f'cot is OK: {len(df_cot_gb)==1}')
        print(f'etf is OK: {len(df_etf_gb)==1}')
        raise ValueError(f'ambiguous ID name {OI_ID}')
    
    
    # Step 3: merge oi, cot and etf stuff
    df_oi_single = df_oi[df_oi.Product_Description == OI_ID][['trade_date','Open_Interest','Total_Volume']]
    df_oi_single.Open_Interest = df_oi_single.Open_Interest.apply(to_int)
    df_oi_single.Total_Volume = df_oi_single.Total_Volume.astype(float).astype(int)
    df_commod_net = df_cot_single.copy()

    df_commod_net['cot_yyyymmdd'] = df_commod_net.As_of_Date_In_Form_YYMMDD.apply(ju.str_to_yyyymmdd)
    df_commod_net = df_commod_net.sort_values('cot_yyyymmdd')
    df_commod_net.index = list(range(len(df_commod_net)))

    last_date = ju.str_to_date(str(df_commod_net.iloc[-1].cot_yyyymmdd),sep='') + datetime.timedelta(7)
    last_date_yyyymmdd = ju.str_to_yyyymmdd(last_date)
    df_commod_net['next_cot_yyyymmdd'] = list(df_commod_net[1:].cot_yyyymmdd) + [last_date_yyyymmdd]

    df_etf_oi = df_etf_single[['trade_date','nav','shares']].merge(df_oi_single,how='inner',on='trade_date')
    df_etf_oi['nav_diff'] = df_etf_oi.nav.pct_change()
    df_etf_oi['share_diff'] = df_etf_oi.shares.pct_change()
    df_etf_oi['oi_diff'] = df_etf_oi.Open_Interest.pct_change()
    
    df_etf_oi = df_etf_single.copy()
    q = f"select * from df_etf_oi inner join df_commod_net on df_etf_oi.trade_date >= df_commod_net.cot_yyyymmdd and df_etf_oi.trade_date < df_commod_net.next_cot_yyyymmdd"
    df_etf_oi_cot =  psql.sqldf(q, locals())
#     etf_oi_cols = list(df_etf_oi.columns.values)
#     cot_cols = list(cols_to_change.values()) + ['cot_yyyymmdd','next_cot_yyyymmdd']
#     etf_oi_cot_cols = etf_oi_cols + cot_cols
#     df_etf_oi_cot = df_etf_oi_cot[etf_oi_cot_cols]

    # step 4: create final,
    cot_cols = ['prod_net','monman_net','swap_net','other_net','nonrep_net','prod_ratio','monman_ratio','swap_ratio','other_ratio']
    df_final = df_etf_oi_cot[['trade_date','nav']+cot_cols][-1000:]
    df_final = df_final.loc[:,~df_final.columns.duplicated()]
    df_final = df_final.sort_values('trade_date')
    return df_final


In [101]:
create_merged_df('wheat').tail()


using get_barchart_commod for ZWZ99
all ID's for commodity: wheat are OK


trade_date    nav  prod_net  monman_net  swap_net  other_net  \
1350    20200505  542.0  -72430.0      6295.0   75542.0     4408.0   
1351    20200506  539.0  -72430.0      6295.0   75542.0     4408.0   
1352    20200507  544.0  -72430.0      6295.0   75542.0     4408.0   
1353    20200508  544.0  -72430.0      6295.0   75542.0     4408.0   
1354    20200511  539.0  -72430.0      6295.0   75542.0     4408.0   

      nonrep_net  prod_ratio  monman_ratio  swap_ratio  other_ratio  
1350    -13815.0      0.3838      1.093712    4.464753      1.16587  
1351    -13815.0      0.3838      1.093712    4.464753      1.16587  
1352    -13815.0      0.3838      1.093712    4.464753      1.16587  
1353    -13815.0      0.3838      1.093712    4.464753      1.16587  
1354    -13815.0      0.3838      1.093712    4.464753      1.16587

### Create multi plot of all data commodities

In [102]:
import traceback
dict_df = {}
last_n_days = 1000
for k in ID_DICT.keys():
    print(f'processing {k}')
    try:
        df = create_merged_df(k)
        dict_df[k] = df.iloc[-last_n_days:]
    except Exception as e:
        print(f'EXCEPTION: {str(e)}')
#         print(traceback.print_exc())

processing gold
all ID's for commodity: gold are OK
processing silver
all ID's for commodity: silver are OK
processing cotton
all ID's for commodity: cotton are OK
processing soyb
using get_barchart_commod for ZSZ99
all ID's for commodity: soyb are OK
processing soyo
using get_barchart_commod for ZLZ99
all ID's for commodity: soyo are OK
processing wheat
using get_barchart_commod for ZWZ99
all ID's for commodity: wheat are OK
processing corn
all ID's for commodity: corn are OK
processing cl
all ID's for commodity: cl are OK
processing ng
all ID's for commodity: ng are OK
processing hg
all ID's for commodity: hg are OK
processing pl
all ID's for commodity: pl are OK
processing sugar
all ID's for commodity: sugar are OK
processing cocoa
all ID's for commodity: cocoa are OK


___
### Plot each df in dict_df using plotly
___

In [103]:
ddd = dict_df['cl']
net_cols = [c for c in ddd.columns.values if '_net' in c]
f = ju.plotly_plot(ddd[['trade_date','nav']+net_cols],x_column='trade_date',bar_plot=False,yaxis2_cols=['nav'])
iplot(f)

/Users/bperlman1/Virtualenvs3/dashrisk5/lib/python3.6/site-packages/plotly/graph_objs/_deprecations.py:410: DeprecationWarning:

plotly.graph_objs.Margin is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.layout.Margin




In [104]:
f = ju.plotly_plot(ddd[['trade_date','nav','monman_net','other_net']],x_column='trade_date',bar_plot=False,yaxis2_cols=['nav'])
iplot(f)

## COT vs Market Graphs
Run the cell below to create a graph for each commodity which displays both the COT history for that commodity and the price history for that commodity.

In [105]:
dict_df['gold'].tail(15)
dict_df.keys()

dict_keys(['gold', 'silver', 'cotton', 'soyb', 'soyo', 'wheat', 'corn', 'cl', 'ng', 'hg', 'pl', 'sugar', 'cocoa'])

In [106]:
y_left_label = 'y nav'
y_right_label = 'monman_net'

df_all_in = None
for k in dict_df.keys():
    df_in = dict_df[k]
    if len(df_in)>1:
        df_in_with_commod = df_in.copy()
        df_in_with_commod['symbol'] = k
        if df_all_in is None:
            df_all_in = df_in_with_commod.copy()
        else:
            df_all_in = df_all_in.append(df_in_with_commod,ignore_index=True)
    last_date = df_in.trade_date.max()
    xc = 'trade_date'
    plot_title = f'{k} last trade date {last_date}'
    try:
        fig = ju.plotly_pandas(df_in[['trade_date', 'nav', y_right_label]],x_column=xc,plot_title=plot_title,y_left_label=y_left_label,y_right_label=y_right_label)
        iplot(fig)
    except Exception as e:
        print(f'{k} {str(e)}')
df_all_in.to_csv(f'{TEMP_FOLDER}/df_all_in.csv',index=False)


In [19]:
# this is the old "non plotly" plotting routine
# ju.multi_df_plot(dict_df=dict_df,x_column='trade_date',num_of_x_ticks=40,save_file_prefix='cot_nav_plot',save_image_folder='./temp_folder/saved_images')    


___
### Try various strategies based on above charts
___

In [20]:
dict_df['cl'].columns.values

array(['trade_date', 'nav', 'prod_net', 'monman_net', 'swap_net',
       'other_net', 'nonrep_net', 'prod_ratio', 'monman_ratio',
       'swap_ratio', 'other_ratio'], dtype=object)

In [21]:
field_to_chart = 'nav'
field_to_chart2 = 'monman_net'
for sym in dict_df.keys():
    df_all_in = dict_df[sym].copy()    
    df_all_in[f'{field_to_chart2}_prev'] = df_all_in[field_to_chart2].shift(1)
    df_all_in['is_transition'] = df_all_in.apply(lambda r: 1 if r[field_to_chart2] / r[f'{field_to_chart2}_prev'] < 0 else 0,axis=1)
    df_all_in['trans_sign'] = df_all_in.apply(lambda r: 1 if r[field_to_chart2] - r[f'{field_to_chart2}_prev'] > 0 else -1,axis=1)
    df_all_in['transition'] = df_all_in.is_transition * df_all_in.trans_sign
    df_all_in2 = df_all_in[['trade_date',field_to_chart,'transition']]
    fig = ju.plotly_pandas(df_all_in2[['trade_date',field_to_chart,'transition']],x_column='trade_date',plot_title=sym)
    iplot(fig)
# len(df_all_in[df_all_in.tran_count==1])/len(df_all_in)

___
### The cells below help you find commodities in df_cot2 and df_oi
___

In [22]:
df_oi[df_oi.Product_Description=='SUGAR 11 FUTURES'].tail()

CME__Globex__Volume Commodity_Indicator  Description ExPit_Volume  \
1166509                  0.0                  YO  AG PRODUCTS            0   
1385247                  7.0                  YO  AG PRODUCTS            0   
1386177                  2.0                  YO  AG PRODUCTS            0   
1387114                  1.0                  YO  AG PRODUCTS            0   
1388082                  0.0                  YO  AG PRODUCTS            0   

        Exchange_Name Future_Option_Indicator MTD_ADV None OTC_Volume  \
1166509  NYMEX(STATS)                       F       0  NaN          0   
1385247  NYMEX(STATS)                       F     3.5  NaN          0   
1386177  NYMEX(STATS)                       F       3  NaN          0   
1387114  NYMEX(STATS)                       F     2.5  NaN          0   
1388082  NYMEX(STATS)                       F       2  NaN          0   

         Open_Interest Pit_Volume Product_Description  Total_Volume  \
1166509              0          0    SUGAR 11 FUTURES             0   
1385247              3          0    SUGAR 11 FUTURES             7   
1386177              1          0    SUGAR 11 FUTURES             2   
1387114              0          0    SUGAR 11 FUTURES             1   
1388082              0          0    SUGAR 11 FUTURES             0   

         trade_date  
1166509    20180702  
1385247    20190604  
1386177    20190605  
1387114    20190606  
1388082    20190607

In [23]:
list(filter(lambda s: str(s)!='nan' and 'COCOA' in s and 'FUTURE' in s,list(set(df_oi.Product_Description))))

['COCOA FUTURES']

In [24]:
list(filter(lambda s: str(s)!='nan' and 'COCOA' in s ,list(set(df_cot2.Market_and_Exchange_Names))))

['COCOA - ICE FUTURES U.S.']

In [25]:
print(df_cot2[df_cot2.Market_and_Exchange_Names=='COTTON NO. 2 - NEW YORK COTTON EXCHANGE'].Open_Interest_All.sum())
print(df_cot2[df_cot2.Market_and_Exchange_Names=='COTTON NO. 2 - ICE FUTURES U.S.'].Open_Interest_All.sum())


0
63737015


In [26]:
list(filter(lambda s: 'Comm' in s,df_cot2.columns.values))

[]

In [27]:
df_cot2_cl = df_cot2[df_cot2.Market_and_Exchange_Names=='CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE']
df_cot2_cl = df_cot2_cl.sort_values('As_of_Date_In_Form_YYMMDD')
df_cot2_cl.tail()

Market_and_Exchange_Names  \
9371  CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE   
9372  CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE   
9373  CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE   
9374  CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE   
9375  CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE   

     As_of_Date_In_Form_YYMMDD  Open_Interest_All  \
9371                2020-04-07            2342227   
9372                2020-04-14            2353955   
9373                2020-04-21            2276638   
9374                2020-04-28            2261202   
9375                2020-05-05            2243871   

      Prod_Merc_Positions_Long_All  Swap_Positions_Long_All  \
9371                        555045                   126318   
9372                        488323                   138641   
9373                        468562                   146426   
9374                        463745                   133110   
9375                        464901                   136434   

      M_Money_Positions_Long_All  Other_Rept_Positions_Long_All  \
9371                      271865                         383906   
9372                      295870                         404604   
9373                      324667                         411581   
9374                      384326                         353452   
9375                      392191                         330721   

      NonRept_Positions_Long_All  Tot_Rept_Positions_Long_All  \
9371                      118327                      2223900   
9372                      129134                      2224821   
9373                      100919                      2175719   
9374                      102192                      2159010   
9375                       95769                      2148102   

      Prod_Merc_Positions_Short_All  ...  swap_net  swap_ratio  monman_net  \
9371                         540300  ... -539792.0    0.189635    180323.0   
9372                         519210  ... -523942.0    0.209243    195355.0   
9373                         517090  ... -544054.0    0.212064    247478.0   
9374                         539452  ... -514578.0    0.205516    318366.0   
9375                         557148  ... -444651.0    0.234792    328601.0   

      monman_ratio  other_net  other_ratio  nonrep_net  nonrep_ratio  \
9371      2.969839   304572.0     4.839111     40152.0      1.513617   
9372      2.943541   315314.0     4.531347     44160.0      1.519688   
9373      4.206130   339702.0     5.726026      5402.0      1.056555   
9374      5.826653   271022.0     4.287905       897.0      1.008855   
9375      6.167495   202011.0     2.569505      6286.0      1.070248   

      totrep_net  totrep_ratio  
9371    -40152.0      0.982265  
9372    -44160.0      0.980538  
9373     -5402.0      0.997523  
9374      -897.0      0.999585  
9375     -6286.0      0.997082  

[5 rows x 27 columns]

## END

In [28]:
comod = 'hg'
fig = ju.plotly_pandas(dict_df[comod][['trade_date', 'monman_net', 'monman_ratio']],x_column='trade_date',plot_title=comod)
iplot(fig)


In [29]:
def get_cot2(id):
    basic_cols = ['Market_and_Exchange_Names','As_of_Date_In_Form_YYMMDD','Open_Interest_All']
    long_cols = ['M_Money_Positions_Long_All','Other_Rept_Positions_Long_All','Prod_Merc_Positions_Long_All',
                'NonRept_Positions_Long_All']
    short_cols = ['M_Money_Positions_Short_All','Other_Rept_Positions_Short_All','Prod_Merc_Positions_Short_All',
                'NonRept_Positions_Short_All']

    df_ret = df_cot2[df_cot2.Market_and_Exchange_Names==ID_DICT[id]['COT']]
    df_ret = df_ret[basic_cols + long_cols + short_cols]
    return df_ret
dfc = get_cot2('cl')

In [30]:
get_cot2('cl').columns.values

array(['Market_and_Exchange_Names', 'As_of_Date_In_Form_YYMMDD',
       'Open_Interest_All', 'M_Money_Positions_Long_All',
       'Other_Rept_Positions_Long_All', 'Prod_Merc_Positions_Long_All',
       'NonRept_Positions_Long_All', 'M_Money_Positions_Short_All',
       'Other_Rept_Positions_Short_All', 'Prod_Merc_Positions_Short_All',
       'NonRept_Positions_Short_All'], dtype=object)

In [31]:
dfc[dfc.As_of_Date_In_Form_YYMMDD=='2019-04-23']

Market_and_Exchange_Names  \
9322  CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE   

     As_of_Date_In_Form_YYMMDD  Open_Interest_All  M_Money_Positions_Long_All  \
9322                2019-04-23            2139213                      352453   

      Other_Rept_Positions_Long_All  Prod_Merc_Positions_Long_All  \
9322                         292217                        448757   

      NonRept_Positions_Long_All  M_Money_Positions_Short_All  \
9322                       96400                        22057   

      Other_Rept_Positions_Short_All  Prod_Merc_Positions_Short_All  \
9322                           75254                         507806   

      NonRept_Positions_Short_All  
9322                        73290

In [32]:
dfc = df_cot2[df_cot2.Market_and_Exchange_Names==ID_DICT['cl']['COT']]

In [33]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    print(dfc[dfc.As_of_Date_In_Form_YYMMDD=='2019-04-23'].iloc[0])


Market_and_Exchange_Names         CRUDE OIL, LIGHT SWEET - NEW YORK MERCANTILE EXCHANGE
As_of_Date_In_Form_YYMMDD                                           2019-04-23 00:00:00
Open_Interest_All                                                               2139213
Prod_Merc_Positions_Long_All                                                     448757
Swap_Positions_Long_All                                                          158645
M_Money_Positions_Long_All                                                       352453
Other_Rept_Positions_Long_All                                                    292217
NonRept_Positions_Long_All                                                        96400
Tot_Rept_Positions_Long_All                                                     2042813
Prod_Merc_Positions_Short_All                                                    507806
Swap_Positions_Short_All                                                         670065
M_Money_Positions_Short_All     

In [34]:
from collections import OrderedDict
dfc2 = dfc.to_dict()#('rows')
dfc3 = OrderedDict(sorted(dfc2.items(), key=lambda x: dfc.columns.get_loc(x[0])))

In [35]:
dfc.columns.get_loc(list(dfc2.items())[2][0])

2

In [36]:
pd.DataFrame(dfc.to_dict('rows')).columns.values

array(['Market_and_Exchange_Names', 'As_of_Date_In_Form_YYMMDD',
       'Open_Interest_All', 'Prod_Merc_Positions_Long_All',
       'Swap_Positions_Long_All', 'M_Money_Positions_Long_All',
       'Other_Rept_Positions_Long_All', 'NonRept_Positions_Long_All',
       'Tot_Rept_Positions_Long_All', 'Prod_Merc_Positions_Short_All',
       'Swap_Positions_Short_All', 'M_Money_Positions_Short_All',
       'Other_Rept_Positions_Short_All', 'NonRept_Positions_Short_All',
       'Tot_Rept_Positions_Short_All', 'prod_net', 'prod_ratio',
       'swap_net', 'swap_ratio', 'monman_net', 'monman_ratio',
       'other_net', 'other_ratio', 'nonrep_net', 'nonrep_ratio',
       'totrep_net', 'totrep_ratio'], dtype=object)

In [37]:
dfc.columns.values#.get_loc(key='Open_Interest_All')

array(['Market_and_Exchange_Names', 'As_of_Date_In_Form_YYMMDD',
       'Open_Interest_All', 'Prod_Merc_Positions_Long_All',
       'Swap_Positions_Long_All', 'M_Money_Positions_Long_All',
       'Other_Rept_Positions_Long_All', 'NonRept_Positions_Long_All',
       'Tot_Rept_Positions_Long_All', 'Prod_Merc_Positions_Short_All',
       'Swap_Positions_Short_All', 'M_Money_Positions_Short_All',
       'Other_Rept_Positions_Short_All', 'NonRept_Positions_Short_All',
       'Tot_Rept_Positions_Short_All', 'prod_net', 'prod_ratio',
       'swap_net', 'swap_ratio', 'monman_net', 'monman_ratio',
       'other_net', 'other_ratio', 'nonrep_net', 'nonrep_ratio',
       'totrep_net', 'totrep_ratio'], dtype=object)

In [38]:
pd.DataFrame(dfc2).columns.values == dfc.columns.values

array([ True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True])

In [39]:
df_temp = pd.read_csv(f'{cme_csv_save_folder}/cme_open_interest_2019.csv')#[['trade_date','Open_Interest']]
df_temp = df_temp.sort_values('trade_date')
df_temp = df_temp[df_temp.Commodity_Indicator=='NG'][['trade_date','Open_Interest']]
df_temp.index = list(range(len(df_temp)))
ju.plotly_plot(df_temp,x_column='trade_date',bar_plot=False)

/Users/bperlman1/Virtualenvs3/dashrisk5/lib/python3.6/site-packages/plotly/graph_objs/_deprecations.py:410: DeprecationWarning:

plotly.graph_objs.Margin is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.layout.Margin




### END